# Running the MILP example model
This notebook will show you how to load, build, solve, and examine the results of the MILP example model.

In [ ]:
import calliope

# We increase logging verbosity
calliope.set_log_verbosity("INFO", include_solver_output=False)

## Load model and examine inputs

In [ ]:
model = calliope.examples.milp()

Model inputs can be viewed at `model.inputs`.
Variables are indexed over any combination of `techs`, `nodes`, `carriers`, `costs` and `timesteps`.

In [ ]:
model.inputs

Individual data variables can be accessed easily, `to_series().dropna()` allows us to view the data in a nice tabular format.

In [ ]:
model.inputs.flow_cap_max.to_series().dropna()

You can apply node/tech/carrier/timesteps only operations, like summing information over timesteps

In [ ]:
model.inputs.sink_use_equals.sum(
    "timesteps", min_count=1, skipna=True
).to_series().dropna()

## Build and solve the optimisation problem.

Results are loaded into `model.results`.
By setting the log verbosity at the start of this tutorial to "INFO", we can see the timing of parts of the run, as well as the solver's log.

In [ ]:
model.build()
model.solve()

Model results are held in the same structure as model inputs.
The results consist of the optimal values for all decision variables, including capacities and carrier flow.
There are also results, like system capacity factor and levelised costs, which are calculated in postprocessing before being added to the results Dataset

## Examine results

In [ ]:
model.results

Integer variables `purchased_units` and `operating_units` are available in the results

In [ ]:
model.results.purchased_units.to_series().dropna()

In [ ]:
model.results.operating_units.to_series().dropna().unstack("techs").head()

We can sum heat output over all locations and turn the result into a pandas DataFrame.

Note: heat output of transmission technologies (e.g., `N1_to_X2`) is the import of heat at nodes.

In [ ]:
df_heat = (
    model.results.flow_out.sel(carriers="heat")
    .sum("nodes", min_count=1, skipna=True)
    .to_series()
    .dropna()
    .unstack("techs")
)

df_heat.head()

You can apply node/tech/carrier only operations, like summing information over nodes

In [ ]:
df_heat.info()

We can also examine total technology costs.

In [ ]:
costs = model.results.cost.to_series().dropna()
costs

We can also examine levelized costs for each location and technology, which is calculated in a post-processing step.

In [ ]:
lcoes = (
    model.results.systemwide_levelised_cost.sel(carriers="electricity")
    .to_series()
    .dropna()
)
lcoes

---

See the [Calliope documentation](https://calliope.readthedocs.io/) for more details on setting up and running a Calliope model.